### HW10 Solution (SNAP Dataset)
- 무방향 그래프 + 엣지 가중치 합산
- Degree / PageRank 상위 10 비교
- Louvain 커뮤니티 시각화
- 핵심 노드(5) ego-subgraph PDF 저장
- 선택: pyvis HTML 생성

In [1]:
import os, sys, gzip, platform
from collections import defaultdict
import pandas as pd
import networkx as nx
import matplotlib
import matplotlib.pyplot as plt
matplotlib.use('Agg')  # 노트북 밖 저장용 (노트북에서 보려면 주석 처리)
try:
    import community as community_louvain
except Exception:
    raise RuntimeError("Install: pip install python-louvain")

EDGE_FILE = "./email-Eu-core.txt.gz"  # 수정하세요
DELIM = "space"  # 'space'|'tab'|'csv'
WEIGHTED = False
OUTDIR = "./outputs"
TOPK = 10
EGO = 5
os.makedirs(OUTDIR, exist_ok=True)

print("Python:", platform.python_version())
print("networkx:", nx.__version__)

Python: 3.13.9
networkx: 3.5


In [2]:
def read_edges(edge_file, delimiter='space', weighted=False):
    open_fn = gzip.open if edge_file.endswith('.gz') else open
    sep = {'space': None, 'tab': '\t', 'csv': ','}[delimiter]
    with open_fn(edge_file, 'rt', encoding='utf-8', errors='ignore') as f:
        for line in f:
            if not line.strip():
                continue
            if line.startswith('#') or line.startswith('%'):
                continue
            parts = line.strip().split(sep)
            if len(parts) < 2:
                continue
            u, v = parts[0], parts[1]
            if weighted:
                w = float(parts[2]) if len(parts) >= 3 else 1.0
            else:
                w = 1.0
            if u == v:
                continue
            yield (u, v, w)

def build_undirected_weighted_graph(edges):
    agg = defaultdict(float)
    for u, v, w in edges:
        a, b = (u, v) if u <= v else (v, u)
        agg[(a, b)] += w
    G = nx.Graph()
    for (u, v), w in agg.items():
        G.add_edge(u, v, weight=w)
    return G

In [3]:
edges = read_edges(EDGE_FILE, delimiter=DELIM, weighted=WEIGHTED)
G = build_undirected_weighted_graph(edges)
print(f"Graph built: |V|={G.number_of_nodes()} |E|={G.number_of_edges()}")

deg = nx.degree_centrality(G)
pr = nx.pagerank(G, alpha=0.85, weight='weight')

df = pd.DataFrame({
    'Degree': pd.Series(deg),
    'PageRank': pd.Series(pr)
})
top = df.sort_values(['Degree', 'PageRank'], ascending=False).head(TOPK)
top.to_csv(os.path.join(OUTDIR, 'top10_degree_pagerank.csv'), encoding='utf-8')
top.head()

Graph built: |V|=986 |E|=16064


Degree  PageRank
160  0.350254  0.009588
121  0.235533  0.006594
82   0.234518  0.006078
107  0.222335  0.006560
86   0.219289  0.006274

In [4]:
part = community_louvain.best_partition(G, weight='weight', random_state=42)
pos = nx.spring_layout(G, seed=42)
import pandas as pd
communities = pd.Series(part).astype('category')
colors = communities.cat.codes

plt.figure(figsize=(10,8))
nx.draw_networkx_edges(G, pos, alpha=0.15, width=0.5)
nx.draw_networkx_nodes(G, pos, node_color=colors, cmap='tab20', node_size=20, linewidths=0)
plt.axis('off')
plt.title('Louvain Communities (colored)')
plt.tight_layout()
plt.savefig(os.path.join(OUTDIR, 'communities_louvain.png'), dpi=220)
plt.close()
communities.value_counts().head()

2    337
5    237
1    146
0    115
4     95
Name: count, dtype: int64

In [5]:
deg_series = pd.Series(deg).sort_values(ascending=False)
hubs = list(deg_series.head(EGO).index)
ego_dir = os.path.join(OUTDIR, 'ego_pdfs')
os.makedirs(ego_dir, exist_ok=True)
for node in hubs:
    ego = nx.ego_graph(G, node, radius=1, undirected=True)
    pos_e = nx.spring_layout(ego, seed=42)
    plt.figure(figsize=(7,6))
    nx.draw_networkx_edges(ego, pos_e, alpha=0.4)
    sizes = [200 if n != node else 600 for n in ego.nodes()]
    colors = ['#9ecae1' if n != node else '#de2d26' for n in ego.nodes()]
    nx.draw_networkx_nodes(ego, pos_e, node_size=sizes, node_color=colors, edgecolors='black', linewidths=0.5)
    nx.draw_networkx_labels(ego, pos_e, font_size=8)
    plt.title(f'Ego subgraph (center={node})')
    plt.axis('off')
    plt.tight_layout()
    plt.savefig(os.path.join(ego_dir, f'ego_{str(node)}.pdf'))
    plt.close()
hubs

['160', '121', '82', '107', '86']